# NB #2:  Arbitrage 

### Pool address: 0x8b6e6E7B5b3801FEd2CaFD4b22b8A16c2F2Db21a  -- 80% WETH - 20% DAI 

The Balancer Pool cadCAD model provides a core infrastructure for simulating Balancer Pools in the **Token Engineering Design and Verification process**.

It allows to simulate Balancer Pool transactions and verify new designs and application cases.  
In this notebook we plug **historical on-chain data** to a cadCAD model, and analyse **Pool Power** and **Pool Characteristics**.

For more information check out the [Balancer Simulations documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/).

# A. System Context

### A1.1 System Specification
System specification details are available in the Balancer Simulations documentation:
- [Differential Specification](https://token-engineering-balancer.gitbook.io/balancer-simulations/balancer-simulations/v10nboverview)
- [Mathematical Specification](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/balancer-the-python-edition/balancer_math.py)
- [Model Architecture](https://token-engineering-balancer.gitbook.io/balancer-simulations/balancer-simulations/v10nboverview)
- [Naming Convention](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/naming-convention)

# B. cadCAD Simulations

### B1.1 Dependencies

In [1]:
import pandas as pd 
from cadCAD.configuration.utils import config_sim
from model.models import Token, Pool
from model.parts.pool_method_entities import TokenAmount

### B1.2 Initialize Pool


In this section you specify the Balancer Pool to be analyzed and run scripts to produce the'genesis_state', based on on-chain data. 

More information here: [Balancer Simulations documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/onchaintransactions).  

In [2]:
import pprint
pp = pprint.PrettyPrinter(indent=4)

from decimal import Decimal

# No spot_price_reference means all pairs are calculated.
parameters = {
    'decoding_type': ['SIMPLIFIED'],
    'external_currency': ['USD'],
    'max_arb_liquidity': [100000],
    'min_arb_liquidity': [10],
    'arb_liquidity_granularity': [50],
    'weight_changing': [False]
    
}


#### Create your pool

Create your genesis states using our Token and Pool classes. Pool will check for token weight integrity

Token prices could come from initial state files

// TODO document
Learn more how to create this variables [documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/v/master/todo).


In [3]:
from model.genesis_states import generate_initial_state


tokens = {
    'DAI': Token(denorm_weight=10, balance=Decimal('10000000'), bound=True),
    'WETH': Token(denorm_weight=40, balance=Decimal('67738.636173102396002749'), bound=True)
}
generated_fees = {
    'WETH': Decimal('0'),
    'DAI': Decimal('0')
}    
initial_values = {
    'pool': Pool(tokens=tokens,
               generated_fees=generated_fees,
               shares=Decimal('100'),
               swap_fee=Decimal('0.0025')),
    
}
initial_values['spot_prices'] = initial_values['pool'].spot_prices(ref_token=None)


print(initial_values)


{'pool': <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 10000000, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67738.636173102396002749, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >, 'spot_prices': {'DAI': {'WETH': Decimal('591.9849127769919849127838632')}, 'WETH': {'DAI': Decimal('0.001697710179777002406083934838')}}}


#### State Variables and Initial Values

In [4]:
print('## State Variables')
print('# Pool')
initial_values['tx_cost'] = TokenAmount(symbol='USD', amount=Decimal(30))
initial_values['token_prices'] = {
        'WETH': Decimal('596.1937868299183'),
        'DAI': Decimal('1.0037648993426744')
    }
initial_values['change_datetime'] = '2020-12-07T13:34:14+00:00'
initial_values['action_type'] = 'pool_creation'

pp.pprint(initial_values)


## State Variables
# Pool
{   'action_type': 'pool_creation',
    'change_datetime': '2020-12-07T13:34:14+00:00',
    'pool': <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 10000000, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67738.636173102396002749, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >,
    'spot_prices': {   'DAI': {   'WETH': Decimal('591.9849127769919849127838632')},
                       'WETH': {   'DAI': Decimal('0.001697710179777002406083934838')}},
    'token_prices': {   'DAI': Decimal('1.0037648993426744'),
                        'WETH': Decimal('596.1937868299183')},
    'tx_cost': 30 USD}


#### External USD Token Prices

In [5]:
print('# External token prices, initial state')
token_prices = initial_values['token_prices']
pp.pprint(token_prices)

print('# Action Type')
action_type = initial_values['action_type']
pp.pprint(action_type)


# External token prices, initial state
{'DAI': Decimal('1.0037648993426744'), 'WETH': Decimal('596.1937868299183')}
# Action Type
'pool_creation'


### B1.3 State Update Functions & Policies

Balancer Simulations replicate Balancer Pool Transactions in state update functions.  
For a detailed description, please visit the [Balancer Simulations documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/balancer-the-python-edition).

### B1.4 Partial State Update Blocks

Partial State Update Blocks combine the following steps:  
1. **Initialize pool**, generate genesis state
2. Compute subsequent **actions in discrete timesteps**, store datetime and update the pool state variables
3. Update external **USD prices in discrete timesteps**, and store datetime  

For more information please visit the [Balancer Simulations documentation/Model Overview](https://token-engineering-balancer.gitbook.io/balancer-simulations/v/master/balancer-simulations/v10nboverview).  

To inject historical on-chain transactions to the model, reference the **actions.json of your pool below**.

In [6]:
from model.partial_state_update_block import generate_partial_state_update_blocks

result = generate_partial_state_update_blocks(path_to_action_json='data/0x8b6e6e7b5b3801fed2cafd4b22b8a16c2f2db21a-actions-prices-only.json',
                                              add_arbitrage=True)
partial_state_update_blocks = result['partial_state_update_blocks']
pp.pprint(partial_state_update_blocks)

[   {   'policies': {   'external_signals': <function ActionDecoder.p_action_decoder at 0x7f905fab7af0>},
        'variables': {   'action_type': <function s_update_action_type at 0x7f905fab7b80>,
                         'change_datetime': <function s_update_change_datetime at 0x7f905fab7040>,
                         'pool': <function s_update_pool at 0x7f905fab7e50>,
                         'spot_prices': <function s_update_spot_prices at 0x7f905fa440d0>,
                         'token_prices': <function s_update_external_price_feeds at 0x7f905fa41790>}},
    {   'policies': {'arbitrage': <function p_arbitrageur at 0x7f905faadee0>},
        'variables': {   'change_datetime': <function s_update_change_datetime at 0x7f905fab7040>,
                         'pool': <function s_update_pool at 0x7f905fab7e50>,
                         'spot_prices': <function s_update_spot_prices at 0x7f905fa440d0>}}]


### B1.5 Configuration

[cadCAD simulations](https://github.com/cadCAD-org/cadCAD/blob/master/documentation/README.md) support Monte Carlo runs, and parameter sweeps which are not applied in this notebook and can be ignored here.  
Timesteps 'T' are defined by your pool's .json file, no need to make edits here.

In [7]:
steps_number = result['steps_number']
print('# Steps ', steps_number)
sim_config = config_sim(
    {
        'N': 1,  # number of monte carlo runs
        'T': range(steps_number - 1),  # number of timesteps
        'M': parameters,  # simulation parameters
    }
)

# Steps  1936


### B1.6 Execution

In [8]:
from model.sim_runner import *
from ipdb import launch_ipdb_on_exception


with launch_ipdb_on_exception():
    df = run(initial_values, partial_state_update_blocks, sim_config)


                  ___________    ____
  ________ __ ___/ / ____/   |  / __ \
 / ___/ __` / __  / /   / /| | / / / /
/ /__/ /_/ / /_/ / /___/ ___ |/ /_/ /
\___/\__,_/\__,_/\____/_/  |_/_____/
by cadCAD

Execution Mode: single_proc
Configuration Count: 1
Dimensions of the first simulation: (Timesteps, Params, Runs, Vars) = (1935, 6, 1, 6)
Execution Method: single_proc_exec
Execution Mode: single_threaded
Timestep 1 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 10000000, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67738.636173102396002749, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.0041752851710719074418420859728939831256866455078125 USD on external markets, can come out via {'WETH': 1.005957910056688226468389560 USD} (token_out)
1 WETH (token_in) is ~595.5119056422337280309875495731830596923828125 USD on external markets, can co

Could not find a trade that made more profit than 2 * 30 USD, aborting
Timestep 10 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9921917.200590631029052195561, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67871.84887482804280953895256, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.004725679526071058234037991496734321117401123046875 USD on external markets, can come out via {'WETH': 1.006032767011547730842501076 USD} (token_out)
1 WETH (token_in) is ~589.746173604638897813856601715087890625 USD on external markets, can come out via {'DAI': 586.0387276262254761095942387 USD} (token_out)
tokens whose spot price is cheaper than external price [(PotentialArbTradeLite(token_in='DAI', token_out='WETH'), 0.9987007505835427)]
calculating optimal trade size
Could not find a trade that made more profit than 2 * 30 USD, aborting
Timestep 11 <P

most_profitable_trade: ArbTradeEvaluation(liquidity_in=49860 USD, token_in=84.92345966842638253203282000 WETH, token_out=49732.64741485514111894044759 DAI, effective_token_out_price_in_external_currency=1.002560744134180531591342584 USD, effective_token_out_price_gap_to_external_price=0.003134514070916555209718284311 USD, tx_cost_in_external_currency=30 USD, profit=125.8876831057952839303224204 USD)
SwapExactAmountInInput(token_in=84.92345966842638253203282000 WETH, min_token_out=0 DAI) SwapExactAmountInOutput(token_out=49732.64741485514111894044759 DAI)
Timestep 19 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9928865.072248264314480261365, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67860.42539529243433603404158, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.0020559855998849574376663440489210188388824462890625 USD on external ma

Could not find a trade that made more profit than 2 * 30 USD, aborting
Timestep 27 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9802327.608573705562531485492, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 68079.33661435754607920801539, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.0047915803081599595003581271157599985599517822265625 USD on external markets, can come out via {'WETH': 0.9962327501130321790846264736 USD} (token_out)
1 WETH (token_in) is ~575.20387031072414174559526145458221435546875 USD on external markets, can come out via {'DAI': 577.2484572550208725950890131 USD} (token_out)
tokens whose spot price is cheaper than external price [(PotentialArbTradeLite(token_in='WETH', token_out='DAI'), 0.9964580469317851)]
calculating optimal trade size
Could not find a trade that made more profit than 2 * 30 USD, aborting
Timeste

most_profitable_trade: ArbTradeEvaluation(liquidity_in=99960 USD, token_in=180.9198159070077417290291830 WETH, token_out=101760.5091428631827984632635 DAI, effective_token_out_price_in_external_currency=0.9823064059129714098418445475 USD, effective_token_out_price_gap_to_external_price=0.01460224725276665802763898215 USD, tx_cost_in_external_currency=30 USD, profit=1455.932115071510297661839957 USD)
SwapExactAmountInInput(token_in=180.9198159070077417290291830 WETH, min_token_out=0 DAI) SwapExactAmountInOutput(token_out=101760.5091428631827984632635 DAI)
Timestep 34 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9587067.874134552887253375428, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 68459.89639024796899988134691, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.004717129253986929171560404938645660877227783203125 USD on external mar

...

most_profitable_trade: ArbTradeEvaluation(liquidity_in=99960 USD, token_in=62.13025918638134345430045250 WETH, token_out=100158.4897454813890813729646 DAI, effective_token_out_price_in_external_currency=0.9980182434261360867987160622 USD, effective_token_out_price_gap_to_external_price=0.004657682060573831234340903014 USD, tx_cost_in_external_currency=30 USD, profit=436.5064009016967017885609998 USD)
SwapExactAmountInInput(token_in=62.13025918638134345430045250 WETH, min_token_out=0 DAI) SwapExactAmountInOutput(token_out=100158.4897454813890813729646 DAI)
Timestep 1906 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 22394444.63980038094202932657, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 55582.92738965859932652111160, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.0026893105468699385340869412175379693508148193359375 USD on external

most_profitable_trade: ArbTradeEvaluation(liquidity_in=99960 USD, token_in=99517.57789128029030387493421 DAI, token_out=62.01325367497803127868690399 WETH, effective_token_out_price_in_external_currency=1611.913487460395081071140686 USD, effective_token_out_price_gap_to_external_price=9.903710383770467232722347652 USD, tx_cost_in_external_currency=30 USD, profit=584.1613043522720156226995373 USD)
SwapExactAmountInInput(token_in=99517.57789128029030387493421 DAI, min_token_out=0 WETH) SwapExactAmountInOutput(token_out=62.01325367497803127868690399 WETH)
Timestep 1913 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 22323982.38982229269925642876, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 55627.46589645459155434618187, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00546031436950489279524845187552273273468017578125 USD on external mark

most_profitable_trade: ArbTradeEvaluation(liquidity_in=99960 USD, token_in=63.30927394099181836177208158 WETH, token_out=101543.3927239222542252593089 DAI, effective_token_out_price_in_external_currency=0.9844067380314226171384764720 USD, effective_token_out_price_gap_to_external_price=0.01652400018344227302915596653 USD, tx_cost_in_external_currency=30 USD, profit=1647.903039997442101186740370 USD)
SwapExactAmountInInput(token_in=63.30927394099181836177208158 WETH, min_token_out=0 DAI) SwapExactAmountInOutput(token_out=101543.3927239222542252593089 DAI)
Timestep 1920 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 22303495.03050987715482963624, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 55641.14375718506126501417776, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.0050019979829210026167629621340893208980560302734375 USD on external 

most_profitable_trade: ArbTradeEvaluation(liquidity_in=99960 USD, token_in=67.22790560404176494981871675 WETH, token_out=104122.7599728530210654375064 DAI, effective_token_out_price_in_external_currency=0.9600206527954278242161695754 USD, effective_token_out_price_gap_to_external_price=0.04188672093187516138369337464 USD, tx_cost_in_external_currency=30 USD, profit=4331.360989639515847940060294 USD)
SwapExactAmountInInput(token_in=67.22790560404176494981871675 WETH, min_token_out=0 DAI) SwapExactAmountInOutput(token_out=104122.7599728530210654375064 DAI)
Timestep 1926 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 21685758.30365656504214687313, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 56034.21149504097625100458650, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.001605592176983083874119984102435410022735595703125 USD on external m

most_profitable_trade: ArbTradeEvaluation(liquidity_in=99960 USD, token_in=70.16371413112465162405852906 WETH, token_out=104845.3191167690206074416813 DAI, effective_token_out_price_in_external_currency=0.9534045090622680945258051786 USD, effective_token_out_price_gap_to_external_price=0.05724073543476387476270894080 USD, tx_cost_in_external_currency=30 USD, profit=5971.423173136366754739328361 USD)
SwapExactAmountInInput(token_in=70.16371413112465162405852906 WETH, min_token_out=0 DAI) SwapExactAmountInOutput(token_out=104845.3191167690206074416813 DAI)
Timestep 1932 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 21071500.21086238383796123863, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 56439.20249220622639585278918, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.015823838663806100157671608030796051025390625 USD on external markets

### B1.7 Simulation Output Preparation

Post-processing (utils.py) splits up state variable dictionaries, and adds metrics to the data frame, such as 
- `token_total_value` (TVL)
- `generated_fees_(tokensymbol)` (fee collected per transaction)
- `token_k_values`  (token value in USD)  
based on  
- `token_k_balances`
- `token_k_price`  (external price feed)

In [9]:
from model.parts.utils import post_processing
p_df = post_processing(df, include_spot_prices=True)
p_df = p_df[p_df['substep'] == 2]
p_df.tail()

pool  \
3862  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3864  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3866  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3868  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3870  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   

                                            spot_prices tx_cost  \
3862  {'DAI': {'WETH': 1497.137454502501481932320231...  30 USD   
3864  {'DAI': {'WETH': 1488.017487390065216164339411...  30 USD   
3866  {'DAI': {'WETH': 1479.053014029413344745356367...  30 USD   
3868  {'DAI': {'WETH': 1479.053014029413344745356367...  30 USD   
3870  {'DAI': {'WETH': 1470.155734344182341381329275...  30 USD   

                                           token_prices  \
3862  {'DAI': 1.010645244497032, 'WETH': 1424.668024...   
3864  {'DAI': 1.015823838663806, 'WETH': 1445.515630...   
3866  {'DAI': 1.006920828125983, 'WETH': 1459.901131...   
3868  {'DAI': 1.011269757254227, 'WETH': 1484.140462...   
3870  {'DAI': 1.011269757254227, 'WETH': 1460.303461...   

               change_datetime            action_type  simulation  subset  \
3862 2021-02-26 08:00:15+00:00  external_price_update           0       0   
3864 2021-02-26 09:00:15+00:00  external_price_update           0       0   
3866 2021-02-26 10:00:15+00:00  external_price_update           0       0   
3868                       NaT  external_price_update           0       0   
3870 2021-02-26 12:00:15+00:00  external_price_update           0       0   

      run  substep  ...  pool_shares token_dai_price  token_weth_price  \
3862    1        2  ...          100        1.010645       1424.668024   
3864    1        2  ...          100        1.015824        1445.51563   
3866    1        2  ...          100        1.006921       1459.901132   
3868    1        2  ...          100         1.01127       1484.140462   
3870    1        2  ...          100         1.01127       1460.303462   

      token_spot_price_dai_weth  token_spot_price_weth_dai  token_dai_value  \
3862                1497.137455                   0.000671     2.129581e+07   
3864                1488.017487                   0.000675     2.130061e+07   
3866                1479.053014                   0.000680     2.101215e+07   
3868                1479.053014                   0.000680     2.110290e+07   
3870                1470.155734                   0.000684     2.100134e+07   

      token_weth_value           tvl      invariant  total_token_balances  
3862      8.040713e+07  1.017029e+08  184503.150362          2.112794e+07  
3864      8.168371e+07  1.029843e+08  184503.601932          2.102531e+07  
3866      8.259657e+07  1.036087e+08  184504.048513          2.092431e+07  
3868      8.396795e+07  1.050709e+08  184504.048513          2.092431e+07  
3870      8.271929e+07  1.037206e+08  184504.494433          2.082394e+07  

[5 rows x 32 columns]

# C. Simulation Outcome & Pool Exploration

The plots below offer some keys metrics for pool analysis.

**a) Pool Power:**  
- C1.1 TVL (Total Value Locked) vs. Pool Growth (token balances in the pool, over time)
- C1.2 Token Balances (individual token balances, over time)

**b) Pool Characteristics:**  
- C1.3 Sources of Pool Growth (BPT, Fees)
- C1.4 Token Ratio
- C1.5 Action Types

In [10]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [11]:
print("Observation Time")
print(f"Start: {p_df['change_datetime'].min()}")
print(f"End: {p_df['change_datetime'].max()}")
print(f"Total Observation Period: {p_df['change_datetime'].max() - p_df['change_datetime'].min()}")
print("\n")
print(f"Total No. of Timesteps (incl. Price Updates): {(p_df.iloc[-1]['timestep'])}")
print(f"Total No. of Transactions: {len(p_df[p_df.action_type != 'external_price_update'])}")

Observation Time
Start: 2020-12-07 20:00:15+00:00
End: 2021-02-26 12:00:15+00:00
Total Observation Period: 80 days 16:00:00


Total No. of Timesteps (incl. Price Updates): 1935
Total No. of Transactions: 0


### Balances

In [12]:
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_dai_balance, line=dict(color='#f36315'), name="Balance DAI"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_weth_balance, line=dict(color='red'), name="Balance WETH"), secondary_y=False)

fig.update_layout(title_text='<b>Balances Prices</b>')
fig.update_xaxes(title_text='timestep')

fig.show()  

In [13]:
### Prices

In [14]:
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_dai_price, line=dict(color='blue'), name="External Price DAI"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_weth_price, line=dict(color='green'), name="External Price WETH"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_spot_price_weth_dai, line=dict(color='red'), name="Spot Price WETH DAI"), secondary_y=True)

fig.update_layout(title_text='<b>Balances Prices</b>')
fig.update_xaxes(title_text='timestep')

fig.show()  

### C1.1 TVL & Pool Size Growth

In [15]:
#TVL vs. Pool Size Growth
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.tvl, line=dict(color='#f36315'), name="TVL total_token_value"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep,y=p_df.total_token_balances, line=dict(color='#2C1839'), name="total_token_balance"), secondary_y=True)
fig.update_layout(title_text='<b>TVL vs. Pool Growth</b>')
fig.update_xaxes(title_text='timestep')
fig.update_yaxes(title_text='<b>TVL total_token_value</b> in USD', secondary_y=False)
fig.update_yaxes(title_text='<b>total_token_balance</b> in #', secondary_y=True)
fig.show()  

### C1.1 Pool Invariant & Pool Size Growth

In [16]:
#TVL vs. Pool Size Growth
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.invariant, line=dict(color='#f36315'), name="Invariant in #"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep,y=p_df.total_token_balances, line=dict(color='#2C1839'), name="total_token_balance"), secondary_y=True)
fig.update_layout(title_text='<b>Invariant vs. Pool Growth</b>')
fig.update_xaxes(title_text='timestep')
fig.update_yaxes(title_text='<b>Invariant</b> in #', secondary_y=False,range=[181000, 189000])
fig.update_yaxes(title_text='<b>total_token_balance</b> in #', secondary_y=True)
fig.show()  

### C1.2 Token Balances

In [17]:
#balance growth % (total observation period)
dai_growth = ((p_df.iloc[-1][['token_dai_balance']])-(p_df.iloc[0][['token_dai_balance']]))*100/(p_df.iloc[0][['token_dai_balance']])
weth_growth = ((p_df.iloc[-1][['token_weth_balance']])-(p_df.iloc[0][['token_weth_balance']]))*100/(p_df.iloc[0][['token_weth_balance']])
growth = list(zip(dai_growth, weth_growth)) 
g_df = pd.DataFrame(growth, columns = ['dai_growth','weth_growth' ]).transpose(copy=True).reset_index()
g_df.columns =['token', 'growth']
print(g_df)
#plot
fig = make_subplots(rows=2, cols=2, subplot_titles=('DAI Growth', 'Balance Growth in %', 'WETH Growth'))
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_dai_balance, line=dict(color='#4675ed'), name='token_dai_balance'), row=1, col=1)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_weth_balance, line=dict(color='#4145ab'), name='token_weth_balance'), row=2, col=1)
fig.add_trace(go.Bar(y=g_df.growth, x=g_df.token, marker_color=['#4675ed','#4145ab']), row=1, col=2)
fig.update_layout(height=600, width=1000, showlegend=False, title_text='<b>Balance Growth</b> in observation period')
fig.show()

         token     growth
0   dai_growth  107.67296
1  weth_growth  -16.37671


### C1.3 Sources of Growth 

In [18]:
#Pool Shares
fig = px.line(p_df, x=p_df.timestep,y=p_df.pool_shares)
fig.update_layout(height=300, width=1000, title_text='<b>Pool Shares (BPT)</b>')
fig.update_xaxes(title_text='timestep')
fig.update_yaxes(title_text='<b>pool shares</b> in #', range=[-0.05,102.00])
fig.show()

In [19]:
#Fees
fig = make_subplots(rows=2, cols=1)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.generated_fees_dai, line=dict(color='#4675ed'), name='fees DAI'), row=1, col=1)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.generated_fees_weth, line=dict(color='#4145ab'), name='fees WETH'), row=2, col=1)
fig.update_yaxes(title_text='token amount', secondary_y=False)
fig.update_layout(height=500, width=1000, title_text='<b>Fees Generated</b> per transaction')

In [20]:
# DAI fee events vs. ETH fee events
WETH_fee_events = len(p_df[p_df.generated_fees_weth > 0])
DAI_fee_events = len(p_df[p_df.generated_fees_dai > 0])
values = [DAI_fee_events, WETH_fee_events]
labels = ['DAI fees', 'WETH fees']
fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
fig.update_traces(hoverinfo='label+percent', marker=dict(colors=['#4675ed','#4145ab']))
fig.update_layout(height=500, width=1000, title_text='<b>Fee generating events</b> in total observation time')
fig.show()

In [21]:
#proportions of fee value contribution, in fixed USD value
daif = p_df.groupby('action_type').sum()['generated_fees_dai'].drop(['external_price_update'])
wethf = p_df.groupby('action_type').sum()['generated_fees_weth'].drop(['external_price_update'])
fee_v = pd.concat([daif, wethf], axis=1)

#calculate USD value (define USD value, in this case locked to initial state observation time)
fee_v['DAI_fee_value'] = fee_v.generated_fees_dai*1.0053414509361551 #define DAI price
fee_v['WETH_fee_value'] = fee_v.generated_fees_weth*594.3526451552318 #define WETH price

#add total 
fee_v = fee_v.append(fee_v.sum().rename('total'))
print(fee_v)

#plot pie chart comparing ETH fees vs DAI fees
values = [fee_v.loc['total']['DAI_fee_value'], fee_v.loc['total']['WETH_fee_value']] 
labels = ['DAI_fees', 'WETH_fees']
fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
fig.update_traces(hoverinfo='label+percent', marker=dict(colors=['#4675ed','#4145ab']))
fig.update_layout(height=500, width=1000, title_text="<b>Fee value contribution</b> in USD, in total observation time")
fig.show()

             generated_fees_dai  generated_fees_weth  DAI_fee_value  \
action_type                                                           
total                       0.0                  0.0            0.0   

             WETH_fee_value  
action_type                  
total                   0.0  


In [22]:
# FEE PER DAY/in fixed USD value

#calculate USD value (define USD value, in this case locked to initial state observation time)
fee_t = p_df[['change_datetime']].dropna()
fee_t['DAI_fee_value'] = p_df.generated_fees_dai*1.0053414509361551 #define DAI price
fee_t['WETH_fee_value'] = p_df.generated_fees_weth*594.3526451552318 #define WETH price
daily = fee_t.groupby(pd.Grouper(key='change_datetime',freq='D')).sum() #sum per week

#plot value per week
fig = go.Figure(data=[go.Bar(name='DAI fees', x=daily.index, y=daily.DAI_fee_value, marker_color='#4675ed', offsetgroup=0), go.Bar(name='WETH fees', x=daily.index, y=daily.WETH_fee_value, marker_color='#4145ab', offsetgroup=1)], layout=go.Layout(title='<b>Fees per day</b> in USD', yaxis_title='USD value'))
fig.show()

### C1.4 Token Ratio

In [23]:
events = [0, -1] #Start/End of observation period
ratio = pd.DataFrame(p_df.iloc[events][['token_dai_balance','token_weth_balance']]).transpose(copy=True)
ratio.columns =['start', 'end'] 
#plot
fig = make_subplots(rows=1, cols=2, specs=[[{'type':'domain'}, {'type':'domain'}]])
fig.add_trace(go.Pie(labels=ratio.index, values=ratio.start), 1, 1)
fig.add_trace(go.Pie(labels=ratio.index, values=ratio.end), 1, 2)
fig.update_traces(hoverinfo='label+percent+name', marker=dict(colors=['#4675ed','#4145ab']))
fig.update_layout(height=400, width=1000, title_text='<b>Token Ratio</b> Start/End Observation Period in %')
fig.show()